In [1]:
from datasets import load_dataset
import pickle
import pandas as pd
import numpy as np
from datasets import DownloadConfig

In [2]:
download_config = DownloadConfig(delete_extracted=True)

In [3]:
ds = load_dataset("csv", 
                  data_files="https://zenodo.org/record/3257041/files/xml2csv_alto.csv?download=1", 
                  download_config=download_config)

Using custom data configuration default-0663d2a6043864fc


Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

0 tables [00:00, ? tables/s]

Dataset csv downloaded and prepared to /Users/dvanstrien/.cache/huggingface/datasets/csv/default-0663d2a6043864fc/0.0.0/51cce309a08df9c4d82ffd9363bbe090bf173197fc01a71b034e8594995a1a58. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
def parse_wc(example):
    if wc := example['wc']:
        wc = wc.split(" ")
        wc = [float(x) for x in wc]
        return {"wc": wc}
    else:
        return  {"wc":[] }

In [5]:
ds = ds.map(parse_wc ,num_proc=4, writer_batch_size=3000)

Parameter 'function'=<function parse_wc at 0x15eaa83a0> of the transform datasets.arrow_dataset.Dataset._map_single couldn't be hashed properly, a random hash was used instead. Make sure your transforms and parameters are serializable with pickle or dill for the dataset fingerprinting and caching to work. If you reuse this transform, the caching mechanism will consider it to be different from the previous calls and recompute everything. This warning is only showed once. Subsequent hashing failures won't be showed.


#0:   0%|          | 0/1247025 [00:00<?, ?ex/s]

#2:   0%|          | 0/1247025 [00:00<?, ?ex/s]

#3:   0%|          | 0/1247024 [00:00<?, ?ex/s]

#1:   0%|          | 0/1247025 [00:00<?, ?ex/s]

In [ ]:
!wget -O corpus-language.pkl https://zenodo.org/record/3257041/files/corpus-language.pkl?download=1

In [6]:
with open("corpus-language.pkl","rb") as f:
    data = pickle.load(f)

In [7]:
data

ppn      filename language  confidence
0     PPN646426230  00000045.xml       fr         1.0
1     PPN646426230  00000218.xml       fr         1.0
2     PPN646426230  00000394.xml       fr         1.0
3     PPN646426230  00000071.xml       fr         1.0
4     PPN646426230  00000317.xml       fr         1.0
...            ...           ...      ...         ...
7479  PPN821899872  00000017.xml       de         1.0
7480  PPN821899872  00000510.xml       de         1.0
7481  PPN821899872  00000487.xml       de         1.0
7482  PPN821899872  00000187.xml       de         1.0
7483  PPN821899872  00000274.xml       de         1.0

[4734627 rows x 4 columns]

In [8]:
data['in'] = data['ppn'] + "_" + data['filename']

In [9]:
data = data.drop_duplicates(subset=['in'])

In [10]:
data = data.set_index("in")

In [11]:
data

ppn      filename language  confidence
in                                                                        
PPN646426230_00000045.xml  PPN646426230  00000045.xml       fr         1.0
PPN646426230_00000218.xml  PPN646426230  00000218.xml       fr         1.0
PPN646426230_00000394.xml  PPN646426230  00000394.xml       fr         1.0
PPN646426230_00000071.xml  PPN646426230  00000071.xml       fr         1.0
PPN646426230_00000317.xml  PPN646426230  00000317.xml       fr         1.0
...                                 ...           ...      ...         ...
PPN821899872_00000017.xml  PPN821899872  00000017.xml       de         1.0
PPN821899872_00000510.xml  PPN821899872  00000510.xml       de         1.0
PPN821899872_00000487.xml  PPN821899872  00000487.xml       de         1.0
PPN821899872_00000187.xml  PPN821899872  00000187.xml       de         1.0
PPN821899872_00000274.xml  PPN821899872  00000274.xml       de         1.0

[4697574 rows x 4 columns]

In [12]:
lookup_dict = data.to_dict('index')

In [13]:
def lookup_lang_confidence(example):
    ppn = example['ppn']
    fname = example['file name']
    if match := lookup_dict.get(f"PPN{ppn}_{fname}"):
        return {"language": match['language'],'language_confidence': match['confidence']}
    else:
        return {"language": None,"language_confidence": None}

In [14]:
lookup_lang_confidence(ds['train'][1])

{'language': 'fr', 'language_confidence': 1.0}

In [15]:
ds = ds.map(lookup_lang_confidence, num_proc=4)

#0:   0%|          | 0/1247025 [00:00<?, ?ex/s]

#1:   0%|          | 0/1247025 [00:00<?, ?ex/s]

#2:   0%|          | 0/1247025 [00:00<?, ?ex/s]

#3:   0%|          | 0/1247024 [00:00<?, ?ex/s]

In [16]:
ds

DatasetDict({
    train: Dataset({
        features: ['file name', 'text', 'wc', 'ppn', 'language', 'language_confidence'],
        num_rows: 4988099
    })
})

`analyticaldf.csv` was generated using: https://github.com/elektrobohemian/StabiHacks/tree/master/oai-analyzer

In [17]:
metadata_df = pd.read_csv("data_prep_code/analysis/analyticaldf.csv",
 sep=";",
 low_memory=False)

In [18]:
metadata_df = metadata_df.replace(np.nan, None)
metadata_df.columns

Index(['publisher', 'place', 'date', 'title', 'subTitle', 'language', 'aut',
       'rcp', 'fnd', 'access', 'altoPaths', 'asn', 'ppn', 'oth', 'scr', 'wpr',
       'pbl', 'prt', 'edt', 'ctb', 'dst', 'cmp', 'dte', 'hnr', 'trl', 'wst',
       'art', 'orm', 'isb', 'com', 'pht', 'dto', 'dgg', 'egr', 'ill', 'aft',
       'jug', 'pra', 'rsp', 'ltg', 'arr', 'plt', 'dfd', 'cll', 'lyr', 'cre',
       'wac', 'cns', 'his', 'tra', 'lbt', 'win', 'spk', 'aui', 'wat', 'ant',
       'Unnamed: 56', 'partName', 'chr', 'trc', 'ctg', 'bkd', 'wal', 'dsr',
       'prm', 'cmm', 'col', 'mfr', 'enj'],
      dtype='object')

In [19]:
metadata_df = metadata_df.loc[:,['publisher','place','date','title','aut','ppn']]

In [20]:
metadata_df

publisher             place  date  \
0                              Hampelius  Giessae Hessorum  1620   
1                             Egenolphus          Marpurgi  1614   
2                     Breitkopf & Härtel           Leipsic  1806   
3       Königliche privil. Buchdruckerey        Glückstadt  1719   
4                               Oehmigke            Berlin  1796   
...                                  ...               ...   ...   
121690                              None              None  1856   
121691                              None              None  1857   
121692                              None              None  1858   
121693                              None              None  1859   
121694                              None              None  1860   

                                                    title  \
0       Collegium Ethicum, In Quo De Summo Hominis Bon...   
1                                             De Auguriis   
2       Concerto pour la Flûte avec Accompagnement de ...   
3       Schuldige Condolentz-Zeilen Womit seinem Gelie...   
4       Vorschlag zur Verbesserung des doppelten Leist...   
...                                                   ...   
121690                                        Der Wächter   
121691                                        Der Wächter   
121692                                        Der Wächter   
121693                                        Der Wächter   
121694                                        Der Wächter   

                               aut            ppn  
0          Liebenthal, Christianus  PPN1000000974  
1               Niphus, Augustinus  PPN100000127X  
2                     Danzi, Franz  PPN1000006808  
3         Koltemann, Otto Benedict  PPN1000056597  
4       Böttcher, Johann Friedrich  PPN1000059669  
...                            ...            ...  
121690                        None   PPN74709716X  
121691                        None   PPN747097208  
121692                        None   PPN747097224  
121693                        None   PPN747097240  
121694                        None   PPN747097267  

[121695 rows x 6 columns]

In [21]:
metadata_df = metadata_df.drop_duplicates(subset=['ppn'])

In [22]:
lookup_dict = metadata_df.set_index('ppn').to_dict('index')

In [23]:
lookup_dict['PPN1000000974'].keys()

dict_keys(['publisher', 'place', 'date', 'title', 'aut'])

In [24]:
def lookup_metadata(example):
    ppn = example['ppn']
    if match := lookup_dict.get(f"PPN{ppn}"):
        return {"publisher": match['publisher'],'place': match['place'], 'date': match['date'], 'title': match['title'], 'aut': match['aut']}
    else:
        return {"publisher": None,"place": None, "date": None, "title": None, "aut": None}

In [25]:
lookup_metadata(ds['train'][100])

{'publisher': 'Imprimerie de la Mission Catholique',
 'place': 'Chang-hai',
 'date': '1912',
 'title': 'Les pratiques superstitieuses',
 'aut': 'Doré, Henri'}

In [26]:
ds = ds.map(lookup_metadata, num_proc=4)

#1:   0%|          | 0/1247025 [00:00<?, ?ex/s]

#0:   0%|          | 0/1247025 [00:00<?, ?ex/s]

#2:   0%|          | 0/1247025 [00:00<?, ?ex/s]

#3:   0%|          | 0/1247024 [00:00<?, ?ex/s]

In [30]:
ds['train'][10]

{'file name': '00000236.xml',
 'text': None,
 'wc': [],
 'ppn': '646426230',
 'language': None,
 'language_confidence': None,
 'publisher': 'Imprimerie de la Mission Catholique',
 'place': 'Chang-hai',
 'date': '1912',
 'title': 'Les pratiques superstitieuses',
 'aut': 'Doré, Henri'}

In [48]:
ds.push_to_hub('biglam/berlin_state_library_ocr')

Pushing split train to the Hub.


Pushing dataset shards to the dataset hub:   0%|          | 0/53 [00:00<?, ?it/s]

/usr/local/Caskroom/miniforge/base/envs/biglam/lib/python3.9/site-packages/huggingface_hub/hf_api.py:1948: FutureWarning: `identical_ok` has no effect and is deprecated. It will be removed in 0.11.0.
  warnings.warn(


Deleting unused files from dataset repository:   0%|          | 0/52 [00:00<?, ?it/s]